In [90]:
import numpy as np
import pandas as pd

import astropy

from astropy.timeseries import TimeSeries
from astropy.table import Table
from astropy import units as u
import plotly.graph_objects as go

import lightkurve as lk
from lightkurve.correctors import PLDCorrector
from astropy.coordinates import SkyCoord

from dash import Dash, dcc, html, Input, Output, callback, ctx
import dash_bootstrap_components as dbc
#https://docs.lightkurve.org/tutorials/2-creating-light-curves/2-3-k2-pldcorrector.html#4.-Applying-PLD-to-a-TESS-Light-Curve

from senior experience paper: KOI-4813, KOI-0521, KOI-5869, and KOI-2453

In [25]:
search_result_lc = lk.search_lightcurve('KOI-4813')


In [26]:
print(search_result_lc)  


SearchResult containing 16 data products.

 #       mission      year   author   exptime         target_name          distance
                                         s                                  arcsec 
--- ----------------- ---- ---------- ------- ---------------------------- --------
  0 Kepler Quarter 01 2009     Kepler    1800                kplr004840672      0.0
  1 Kepler Quarter 02 2009     Kepler    1800                kplr004840672      0.0
  2 Kepler Quarter 03 2009     Kepler    1800                kplr004840672      0.0
  3 Kepler Quarter 04 2010     Kepler    1800                kplr004840672      0.0
  4 Kepler Quarter 05 2010     Kepler    1800                kplr004840672      0.0
  5 Kepler Quarter 07 2010     Kepler    1800                kplr004840672      0.0
  6 Kepler Quarter 08 2011     Kepler    1800                kplr004840672      0.0
  7 Kepler Quarter 09 2011     Kepler    1800                kplr004840672      0.0
  8 Kepler Quarter 11 2012     Ke

In [148]:
lc_collection = search_result_lc[search_result_lc.author == "Kepler"].download_all()
# want short exposure times https://www.ut.edu/uploadedFiles/Academics/Acta_Spartae/AS_0601p1Argentieri.pdf
lc_collection_info= search_result_lc[search_result_lc.author == "Kepler"]

In [42]:
lc_collection

LightCurveCollection of 14 objects:
    0: <KeplerLightCurve LABEL="KIC 4840672" QUARTER=1 AUTHOR=Kepler FLUX_ORIGIN=pdcsap_flux>
    1: <KeplerLightCurve LABEL="KIC 4840672" QUARTER=2 AUTHOR=Kepler FLUX_ORIGIN=pdcsap_flux>
    2: <KeplerLightCurve LABEL="KIC 4840672" QUARTER=3 AUTHOR=Kepler FLUX_ORIGIN=pdcsap_flux>
    3: <KeplerLightCurve LABEL="KIC 4840672" QUARTER=4 AUTHOR=Kepler FLUX_ORIGIN=pdcsap_flux>
    4: <KeplerLightCurve LABEL="KIC 4840672" QUARTER=5 AUTHOR=Kepler FLUX_ORIGIN=pdcsap_flux>
    5: <KeplerLightCurve LABEL="KIC 4840672" QUARTER=7 AUTHOR=Kepler FLUX_ORIGIN=pdcsap_flux>
    6: <KeplerLightCurve LABEL="KIC 4840672" QUARTER=8 AUTHOR=Kepler FLUX_ORIGIN=pdcsap_flux>
    7: <KeplerLightCurve LABEL="KIC 4840672" QUARTER=9 AUTHOR=Kepler FLUX_ORIGIN=pdcsap_flux>
    8: <KeplerLightCurve LABEL="KIC 4840672" QUARTER=11 AUTHOR=Kepler FLUX_ORIGIN=pdcsap_flux>
    9: <KeplerLightCurve LABEL="KIC 4840672" QUARTER=12 AUTHOR=Kepler FLUX_ORIGIN=pdcsap_flux>
    10: <KeplerLightCu

In [155]:
lc_collection[0]

<KeplerLightCurve length=1626 LABEL="KIC 4840672" QUARTER=1 AUTHOR=Kepler FLUX_ORIGIN=pdcsap_flux>
       time             flux      ...   pos_corr1      pos_corr2   
                    electron / s  ...      pix            pix      
       Time           float32     ...    float32        float32    
------------------ -------------- ... -------------- --------------
131.51240196308936  7.6917827e+03 ...  9.0776747e-03 -4.1715618e-02
 131.5328366199028  7.6959810e+03 ...  9.0881726e-03 -4.1500472e-02
131.55327117648994  7.6942554e+03 ...  8.9672692e-03 -4.1346982e-02
131.57370563306904  7.6952925e+03 ...  8.7374439e-03 -4.1336384e-02
131.59414018965617  7.6915303e+03 ...  8.8381814e-03 -4.1683424e-02
131.61457484612765  7.6907622e+03 ...  8.8688750e-03 -4.1656967e-02
 131.6350093024812  7.6917886e+03 ...  8.9300554e-03 -4.1637775e-02
 131.6554438587118  7.6898994e+03 ...  9.1093248e-03 -4.1698195e-02
131.67587851495045  7.6881309e+03 ...  8.9055542e-03 -4.1606031e-02
               ...            ... ...            ...            ...
164.80011795373866  7.6586831e+03 ... -1.5771436e-02  5.4198351e-02
164.82055225921795  7.6634858e+03 ... -1.5756940e-02  5.4338560e-02
164.84098646446364  7.6618765e+03 ... -1.5852420e-02  5.4192528e-02
164.86142086970358  7.6593291e+03 ... -1.5903238e-02  5.4587901e-02
164.88185517448437  7.6589692e+03 ... -1.5831498e-02  5.5154435e-02
 164.9022893792644  7.6571665e+03 ... -1.6536217e-02  5.4736491e-02
164.92272368357226  7.6596245e+03 ... -1.6524488e-02  5.5748291e-02
164.94315808788815  7.6614277e+03 ... -1.6984219e-02  5.4949399e-02
 164.9635922919697  7.6642778e+03 ... -1.7415565e-02  5.5177659e-02
164.98402659558633  7.6653784e+03 ... -1.7042859e-02  5.5917062e-02

In [30]:
info_table=lc_collection_info[0].table.to_pandas()

In [31]:
info_table.columns

Index(['intentType', 'obs_collection', 'provenance_name', 'instrument_name',
       'project', 'filters', 'wavelength_region', 'target_name',
       'target_classification', 'sequence_number', 'obs_id', 's_ra', 's_dec',
       'proposal_id', 'proposal_pi', 'dataproduct_type', 'calib_level',
       't_min', 't_max', 't_exptime', 'em_min', 'em_max', 'obs_title',
       't_obs_release', 'proposal_type', 'dataRights', 'mtFlag', 'obsid',
       'objID', 'objID1', 'distance', 'exptime', 'obsID',
       'obs_collection_products', 'dataproduct_type_products', 'description',
       'type', 'dataURI', 'productType', 'productGroupDescription',
       'productSubGroupDescription', 'productDocumentationURL',
       'project_products', 'prvversion', 'proposal_id_products',
       'productFilename', 'size', 'parent_obsid', 'dataRights_products',
       'calib_level_products', 'author', 'mission', '#', 'year', 'sort_order'],
      dtype='object')

In [44]:
info_table[['distance', 's_ra', 's_dec']]

distance        s_ra      s_dec
0       0.0  293.240397  39.949442

In [33]:
loc=SkyCoord.from_name('TIC 1969293164')
loc

<SkyCoord (ICRS): (ra, dec) in deg
    (305.28931331, 41.46235738)>

In [149]:
lc_list = []
for x in range(0, len(lc_collection)-1):
    lc_ind=lc_collection[x].to_pandas().reset_index() 
    lc_list.append(lc_ind)
lc_list


[            time         flux  flux_err  quality  timecorr  centroid_col  \
 0     131.512402  7691.782715  3.541702        0  0.001408    383.139341   
 1     131.532837  7695.980957  3.544420        0  0.001409    383.138757   
 2     131.553271  7694.255371  3.544136        0  0.001410    383.139356   
 3     131.573706  7695.292480  3.545213        0  0.001411    383.139596   
 4     131.594140  7691.530273  3.544178        0  0.001412    383.139285   
 ...          ...          ...       ...      ...       ...           ...   
 1621  164.902289  7657.166504  3.553262        0  0.002799    383.142043   
 1622  164.922724  7659.624512  3.548121        0  0.002800    383.142927   
 1623  164.943158  7661.427734  3.552802        0  0.002800    383.142692   
 1624  164.963592  7664.277832  3.549785        0  0.002801    383.141891   
 1625  164.984027  7665.378418  3.553960        0  0.002802    383.142640   
 
       centroid_row  cadenceno     sap_flux  sap_flux_err  ...  psf_centr1

In [179]:
y=lc_list[0]['sap_flux']
t=lc_list[0]['time']


In [180]:
lc_collection[0]['time'].format


'bkjd'

In [181]:
y_unit=lc_collection[0]['flux'].unit.to_string()
x_unit=lc_collection[0]['time'].format

y_unit

'electron / s'

In [177]:
lc_collection[0].meta

{'INHERIT': True,
 'EXTNAME': 'PRIMARY',
 'EXTVER': 1,
 'TELESCOP': 'Kepler',
 'INSTRUME': 'Kepler Photometer',
 'OBJECT': 'KIC 4840672',
 'KEPLERID': 4840672,
 'RADESYS': 'ICRS',
 'RA_OBJ': 293.240397,
 'DEC_OBJ': 39.949442,
 'EQUINOX': 2000.0,
 'EXPOSURE': 30.8339591,
 'TIMEREF': 'SOLARSYSTEM',
 'TASSIGN': 'SPACECRAFT',
 'TIMESYS': 'TDB',
 'BJDREFI': 2454833,
 'BJDREFF': 0.0,
 'TIMEUNIT': 'd',
 'TELAPSE': 33.49205902,
 'LIVETIME': 30.8339591,
 'TSTART': 131.5021847,
 'TSTOP': 164.99424373,
 'LC_START': 54964.01099382,
 'LC_END': 54997.48122492,
 'DEADC': 0.92063492,
 'TIMEPIXR': 0.5,
 'TIERRELA': 5.78e-07,
 'TIERABSO': <astropy.io.fits.card.Undefined at 0x7fe0864be880>,
 'INT_TIME': 6.01980290327,
 'READTIME': 0.518948526144,
 'FRAMETIM': 6.538751429414,
 'NUM_FRM': 270,
 'TIMEDEL': 0.02043359821692,
 'DATE-OBS': '2009-05-13T00:01:07.136Z',
 'DATE-END': '2009-06-15T11:47:40.562Z',
 'BACKAPP': True,
 'DEADAPP': True,
 'VIGNAPP': True,
 'GAIN': 113.82,
 'READNOIS': 85.683696,
 'NREADOU

In [157]:
title=lc_collection[0].meta['OBJECT']

In [183]:
fig = go.Figure(data=go.Scattergl(x=t, y=y, mode='markers'))
fig.update_layout(yaxis_title=f" SAP Flux [{y_unit}]", xaxis_title=f" days [{x_unit}]", title=f"{title}'s Lightcurve from Quarter {lc_collection[0].quarter}")
fig.show()

In [163]:

lc_collection[0].meta

{'INHERIT': True,
 'EXTNAME': 'PRIMARY',
 'EXTVER': 1,
 'TELESCOP': 'Kepler',
 'INSTRUME': 'Kepler Photometer',
 'OBJECT': 'KIC 4840672',
 'KEPLERID': 4840672,
 'RADESYS': 'ICRS',
 'RA_OBJ': 293.240397,
 'DEC_OBJ': 39.949442,
 'EQUINOX': 2000.0,
 'EXPOSURE': 30.8339591,
 'TIMEREF': 'SOLARSYSTEM',
 'TASSIGN': 'SPACECRAFT',
 'TIMESYS': 'TDB',
 'BJDREFI': 2454833,
 'BJDREFF': 0.0,
 'TIMEUNIT': 'd',
 'TELAPSE': 33.49205902,
 'LIVETIME': 30.8339591,
 'TSTART': 131.5021847,
 'TSTOP': 164.99424373,
 'LC_START': 54964.01099382,
 'LC_END': 54997.48122492,
 'DEADC': 0.92063492,
 'TIMEPIXR': 0.5,
 'TIERRELA': 5.78e-07,
 'TIERABSO': <astropy.io.fits.card.Undefined at 0x7fe0864be880>,
 'INT_TIME': 6.01980290327,
 'READTIME': 0.518948526144,
 'FRAMETIM': 6.538751429414,
 'NUM_FRM': 270,
 'TIMEDEL': 0.02043359821692,
 'DATE-OBS': '2009-05-13T00:01:07.136Z',
 'DATE-END': '2009-06-15T11:47:40.562Z',
 'BACKAPP': True,
 'DEADAPP': True,
 'VIGNAPP': True,
 'GAIN': 113.82,
 'READNOIS': 85.683696,
 'NREADOU

In [170]:
traces={}
for x in range(0, len(lc_collection)-1):
        traces['trace_' + str(x)]=go.Scattergl(x=lc_list[x]['time'], name=f"Quarter {lc_collection[x].quarter}", y=lc_list[x]['sap_flux'])

In [182]:
traces2={}
for x in range(0, len(lc_collection)-1):
        traces2['trace_' + str(x)]=go.Scattergl(x=lc_list[x]['time'], name=f"Quarter {lc_collection[x].quarter}", y=lc_list[x]['flux'])

In [184]:
data=list(traces.values())
fig=go.Figure(data)
fig.update_layout(yaxis_title=f"SAP Flux [{y_unit}]", xaxis_title=f" days [{x_unit}]", title=f"{title}'s Lightcurves")
fig.show()

In [185]:
data2=list(traces2.values())
fig=go.Figure(data2)
fig.update_layout(yaxis_title=f"Flux [{y_unit}]", xaxis_title=f" days [{x_unit}]", title=f"{title}'s Lightcurves")
fig.show()

In [48]:
lc=lc_collection.stitch().flatten(window_length=901).remove_outliers()